## New attempt

In the end, we have an HDF file of GlaThiDa per RGI sub-region.

In [135]:
import pandas as pd
import geopandas as gpd
import shapely.geometry as shpg
import numpy as np
import os
import glob
import progressbar
import time
from oggm import utils, cfg
import warnings
import tables

In [136]:
gtd_dir = './glathida-main/data'
# gtd_dir = './GlaThiDa_2016'

## Read the GTD files

In [137]:
dfs = [pd.read_csv(os.path.join(gtd_dir, 'point.csv'), dtype={'date': 'str', 'elevation_date': 'str', 'flag': 'str'}, low_memory=False)]

for path in glob.glob(os.path.join(gtd_dir, '*', 'point.csv')):
    print(path)
    dfs.append(pd.read_csv(path, dtype={'date': 'str', 'elevation_date': 'str', 'flag': 'str'}, low_memory=False))

df = pd.concat(dfs, ignore_index=True)

df = gpd.GeoDataFrame(
  df, geometry=gpd.points_from_xy(df['longitude'], df['latitude'], crs=4326)
)

./glathida-main/data/lippl-2019-gourdon/point.csv
./glathida-main/data/ncdc-2023/point.csv
./glathida-main/data/ben-pelto-columbia-basin/point.csv
./glathida-main/data/oneel-2011-columbia-bering/point.csv
./glathida-main/data/braun-2018-antarctic-peninsula/point.csv
./glathida-main/data/luyendyk-2003-marie-byrd-land/point.csv
./glathida-main/data/corr-2020-antarctic-peninsula/point.csv
./glathida-main/data/oberreuter-2021-artesonraju/point.csv
./glathida-main/data/benham-2020-canadian-arctic/point.csv
./glathida-main/data/franke-2020-dronning-maud-land/point.csv
./glathida-main/data/goel-2019-ice-rises/point.csv
./glathida-main/data/lambrecht-2019-fedchenko/point.csv
./glathida-main/data/24k-glacier-2019/point.csv
./glathida-main/data/swiss-glacier-thickness-r2020/point.csv
./glathida-main/data/heinrichs-1995-black-rapids/point.csv
./glathida-main/data/conway-2016-black-rapids/point.csv
./glathida-main/data/gacitua-2020-schiaparelli/point.csv


In [138]:
for c in df:
    print(c, df[c].dtype)

survey_id int64
glacier_id float64
profile_id object
point_id object
date object
max_date object
elevation_date object
max_elevation_date object
latitude float64
longitude float64
elevation float64
thickness int64
thickness_uncertainty float64
flag object
remarks object
date_max object
geometry geometry


In [139]:
len(df) - 3854279

1432760

In [140]:
len(df)

5287039

In [141]:
len(df.loc[df.thickness == 0]) / len(df), len(df.loc[df.thickness == 0])

(0.03687640662382101, 194967)

## Read RGI, assign and write

In [145]:
for rgi_version in ['62', '70G', '70C']:
    
    rdf = []
    for reg in range(1, 20):
        rdf.append(gpd.read_file(utils.get_rgi_region_file(f'{reg:02d}', version=rgi_version)))
    rdf = pd.concat(rdf)
    
    if rgi_version == '62':
        rdf = rdf.loc[rdf['Connect'] != 2]
        rdf['rgi_id'] = rdf['RGIId']
    
    joined = gpd.sjoin(df, rdf, how='left', predicate='within')
    
    no_join = joined.loc[joined.rgi_id.isnull()]
    ok_join = joined.loc[~joined.rgi_id.isnull()]
    
    print(rgi_version, len(ok_join) / len(df))
    
    to_write = ok_join[['survey_id', 'date', 'elevation_date', 
                        'latitude', 'longitude', 'elevation', 'thickness', 
                        'thickness_uncertainty', 'flag',
                        'rgi_id']]
    
    with warnings.catch_warnings():
        warnings.simplefilter('ignore', tables.PerformanceWarning)
        to_write.to_hdf(gtd_dir + f'/glathida_2023-11-16_rgi_{rgi_version}.h5', key='data', complevel=5)
    
    file = gtd_dir + f'/glathida_2023-11-16_rgi_{rgi_version}_per_id.h5'
    if os.path.exists(file):
        os.remove(file)

    rids = to_write.rgi_id.unique()
    for rid in rids:
        tt = to_write.loc[to_write.rgi_id == rid].reset_index(drop=True)
        with warnings.catch_warnings():
            warnings.simplefilter('ignore', tables.NaturalNameWarning)
            tt.to_hdf(file, key=rid, append=True, complevel=5)

62 0.8385355205437297


/tmp/ipykernel_2029233/185255322.py:26: PerformanceWarning: 
your performance may suffer as PyTables will pickle object types that it cannot
map directly to c-types [inferred_type->mixed,key->block1_values] [items->Index(['date', 'elevation_date', 'flag', 'rgi_id'], dtype='object')]

  to_write.to_hdf(gtd_dir + f'/glathida_2023-11-16_rgi_{rgi_version}.h5', key='data', complevel=5)


70G 0.8368438364082429


/tmp/ipykernel_2029233/185255322.py:26: PerformanceWarning: 
your performance may suffer as PyTables will pickle object types that it cannot
map directly to c-types [inferred_type->mixed,key->block1_values] [items->Index(['date', 'elevation_date', 'flag', 'rgi_id'], dtype='object')]

  to_write.to_hdf(gtd_dir + f'/glathida_2023-11-16_rgi_{rgi_version}.h5', key='data', complevel=5)


70C 0.8368438364082429


/tmp/ipykernel_2029233/185255322.py:26: PerformanceWarning: 
your performance may suffer as PyTables will pickle object types that it cannot
map directly to c-types [inferred_type->mixed,key->block1_values] [items->Index(['date', 'elevation_date', 'flag', 'rgi_id'], dtype='object')]

  to_write.to_hdf(gtd_dir + f'/glathida_2023-11-16_rgi_{rgi_version}.h5', key='data', complevel=5)


In [153]:
with pd.HDFStore('glathida-main/data/glathida_2023-11-16_rgi_70C_per_id.h5') as store:
    rgi_ids = list(store.keys())
    rgi_ids = np.array([s[1:] for s in rgi_ids])

In [154]:
len(rgi_ids)

1278

In [162]:
dfa = pd.read_hdf('glathida-main/data/glathida_2023-11-16_rgi_70C.h5')

In [163]:
dfa = dfa.loc[['-03-' in c for c in dfa.rgi_id]]

In [164]:
dfa = gpd.GeoDataFrame(
  dfa, geometry=gpd.points_from_xy(dfa['longitude'], dfa['latitude'], crs=4326)
)

In [165]:
dfa.to_file(filename='gtd_reg03.shp.zip', driver='ESRI Shapefile')

/tmp/ipykernel_2029233/2911545548.py:1: UserWarning: Column names longer than 10 characters will be truncated when saved to ESRI Shapefile.
  dfa.to_file(filename='gtd_reg03.shp.zip', driver='ESRI Shapefile')


In [166]:
t - 1

0

In [146]:
t = 1

In [127]:

for c in to_write:
    print(c, to_write[c].dtype)

survey_id int64
date object
elevation_date object
latitude float64
longitude float64
elevation float64
thickness int64
thickness_uncertainty float64
flag object
rgi_id object


In [131]:
to_write = to_write.reset_index(drop=True)

/tmp/ipykernel_2029233/271614285.py:1: PerformanceWarning: 
your performance may suffer as PyTables will pickle object types that it cannot
map directly to c-types [inferred_type->mixed,key->block1_values] [items->Index(['date', 'elevation_date', 'flag', 'rgi_id'], dtype='object')]

  to_write.to_hdf(gtd_dir + '/glathida_2023-11-16_rgi_70G.h5', key='data')


In [48]:
def get_rids():
    with pd.HDFStore('glathida-v3.1.0/data/TTT_RGI_v70C_per_id.h5') as store:
        rgi_ids = list(store.keys())
        return np.array([s[1:] for s in rgi_ids])

In [49]:
%timeit get_rids()

946 ms ± 10.5 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [74]:
def read_data(rid):
    out = None
    try:
        out = pd.read_hdf('glathida-v3.1.0/data/TTT_RGI_v70C_per_id.h5', key=rid)
    except KeyError:
        pass
    return out

In [60]:
%timeit read_data('RGI2000-v7.0-C-02-10810')

16.5 ms ± 218 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)


In [61]:
%timeit read_data('RGI2000-v7.0-C-02-10812')

503 µs ± 11.3 µs per loop (mean ± std. dev. of 7 runs, 1,000 loops each)


In [33]:
t = pd.read_hdf('glathida-v3.1.0/data/TTT_RGI_v70C.h5')

In [39]:
%timeit  pd.read_hdf('glathida-v3.1.0/data/TTT_RGI_v70C.h5')

1.96 s ± 99.2 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [35]:
%timeit t.loc[t.rgi_id == 'RGI2000-v7.0-C-02-10810']

191 ms ± 8.26 ms per loop (mean ± std. dev. of 7 runs, 10 loops each)


In [37]:
%timeit t.loc[t.rgi_id == 'RGI2000-v7.0-C-02-10210']

192 ms ± 5.84 ms per loop (mean ± std. dev. of 7 runs, 10 loops each)


In [38]:
t.loc[t.rgi_id == 'RGI2000-v7.0-C-02-10810']

GlaThiDa_ID POLITICAL_UNIT    GLACIER_NAME SURVEY_DATE PROFILE_ID  \
0               33             US          EASTON    19929999        NaN   
1               33             US          EASTON    19929999        NaN   
2               33             US          EASTON    19929999        NaN   
3               33             US          EASTON    19929999        NaN   
4               33             US          EASTON    19929999        NaN   
...            ...            ...             ...         ...        ...   
19089          502             US  SHERMAN CRATER    20109999        NaN   
19090          502             US  SHERMAN CRATER    20109999        NaN   
19091          502             US  SHERMAN CRATER    20109999        NaN   
19092          502             US  SHERMAN CRATER    20109999        NaN   
19093          502             US  SHERMAN CRATER    20109999        NaN   

      POINT_ID  POINT_LAT   POINT_LON  ELEVATION  THICKNESS  \
0            1  48.767380 -121.819644     2962.0          0   
1            2  48.764904 -121.821909     2813.0         29   
2            3  48.761662 -121.825264     2598.0         41   
3            4  48.757063 -121.829107     2383.0         71   
4            5  48.753715 -121.832006     2284.0         82   
...        ...        ...         ...        ...        ...   
19089       76  48.768840 -121.816270     2931.0         59   
19090       77  48.768892 -121.816151     2928.0         54   
19091       78  48.768944 -121.816032     2926.0         51   
19092       79  48.768990 -121.815914     2923.0         49   
19093       80  48.769043 -121.815795     2921.0         43   

       THICKNESS_UNCERTAINTY  DATA_FLAG REMARKS                   rgi_id  
0                        NaN        NaN     NaN  RGI2000-v7.0-C-02-10810  
1                        NaN        NaN     NaN  RGI2000-v7.0-C-02-10810  
2                        NaN        NaN     NaN  RGI2000-v7.0-C-02-10810  
3                        NaN        NaN     NaN  RGI2000-v7.0-C-02-10810  
4                        NaN        NaN     NaN  RGI2000-v7.0-C-02-10810  
...                      ...        ...     ...                      ...  
19089                    5.0        NaN     NaN  RGI2000-v7.0-C-02-10810  
19090                    5.0        NaN     NaN  RGI2000-v7.0-C-02-10810  
19091                    5.0        NaN     NaN  RGI2000-v7.0-C-02-10810  
19092                    5.0        NaN     NaN  RGI2000-v7.0-C-02-10810  
19093                    5.0        NaN     NaN  RGI2000-v7.0-C-02-10810  

[2533 rows x 14 columns]

## Add the RGI Region attribute 

In [9]:
reg = np.ones(len(df), dtype=int) * -1
prev_reg = None
for i, p in progressbar.progressbar(enumerate(df.geometry), max_value=len(df)):
    if prev_reg is not None and prev_reg.contains(p):
        reg[i] = reg[i-1]
        continue
    try:
        sel = rgi_reg.loc[rgi_reg.contains(p)].iloc[0]
        reg[i] = sel.RGI_CODE
        prev_reg = sel.geometry
    except:
        prev_reg = None

100% (3854279 of 3854279) |##############| Elapsed Time: 0:01:44 Time:  0:01:44


In [10]:
df['RGI_REG'] = reg
sorted(df['RGI_REG'].unique())

[1, 2, 3, 4, 5, 7, 8, 10, 11, 12, 13, 16, 17, 18, 19]

## Separate the data in RGI Regions

In [11]:
dfs = OrderedDict()
for r in sorted(df['RGI_REG'].unique()):
    dfs[r] = df.loc[df.RGI_REG == r].copy()

### Prepare for writing and write to file 

In [12]:
for i, (k, d) in enumerate(dfs.items()):
    d.drop(['geometry'], axis=1, inplace=True)
    d['RGI_REG'] = d['RGI_REG'].astype(str)
    d['ELEVATION'] = d['ELEVATION'].astype(str)

In [13]:
for c in d:
    print(c, d[c].dtype)

GlaThiDa_ID int64
POLITICAL_UNIT object
GLACIER_NAME object
SURVEY_DATE object
PROFILE_ID object
POINT_ID object
POINT_LAT float64
POINT_LON float64
ELEVATION object
THICKNESS int64
THICKNESS_UNCERTAINTY float64
DATA_FLAG float64
REMARKS object
RGI_REG object


In [14]:
outf = os.path.join(gtd_dir, 'TTT_per_reg.h5')
if os.path.exists(outf):
    os.remove(outf)
count = 0
for i, (k, d) in enumerate(dfs.items()):
    key = '{:02d}'.format(int(k))
    print('Writing', key, len(d))
    with warnings.catch_warnings():
        warnings.simplefilter('ignore', tables.NaturalNameWarning)
        d.to_hdf(outf, key, append=True, complevel=5)
        count += len(d)
assert count == len(df)

Writing 01 87157
Writing 02 3406
Writing 03 868346
Writing 04 309453
Writing 05 557136
Writing 07 966408
Writing 08 10801
Writing 10 7726
Writing 11 478312
Writing 12 2278
Writing 13 15327
Writing 16 1287
Writing 17 8463
Writing 18 619
Writing 19 537560
